In [26]:
import csv
from apikeys import TMDB_KEY
import requests
import operator
from data.sentiments_nrc import SENTIMENTS, EMOTIONS

In [ ]:
with open('Oscar2019Tweets.csv') as csvfile:
    csvfile.readline()
    csvreader=csv.reader(csvfile)
    csv_data=[]
    for line in csvreader:
        csv_data.append(line)

In [2]:
tweets_data=[]
for row in range(len(csv_data)):
    tweets_data.append(csv_data[row][3])


In [3]:
tweets_info=[]
for row in range(len(csv_data)):
    tweets_info.append(csv_data[row][3].lower())

In [4]:
tweets_info[:5]

['rt @teapainusa: the cheers when you are indicted will drown out the collective roar of the world’s rivers, seas and oceans for the span of…',
 'rt @ladygaganownet: lady gaga &amp; madonna last night at #oscars after-party. https://t.co/836nptnaie',
 'rt @satlokchannel: "intoxication is not meant for human beings. it turns a human being into a devil." - spiritual leader saint rampal ji ma…',
 'taylor swift and joe alwyn packed on the pda at an #oscars after-party and the video is too cute… https://t.co/t3bxzpscmx',
 'gracias a la vida por chris evan #oscars']

In [5]:
from nltk.tokenize import word_tokenize
def extract_words(text):
    raw_words = word_tokenize(text)
    words = []
    for word in raw_words:
        if(word[0].isalpha()):
            words.append(word.lower())
    return words

In [181]:
def clean_list (tweets_data):
    words_list=[]
    for text in tweets_data:
        words_list.append(extract_words(text))
    cleaned_list=[]
    for row in range(len(words_list)):
        for item in range(len(words_list[row])):
            if len(words_list[row][item]) > 2:
                if not words_list[row][item] == 'https':
                    cleaned_list.append(words_list[row][item])
    return(cleaned_list)
    
    

In [92]:
def old_clean_list (tweets_data):
    words_list=[]
    for text in tweets_data:
        words_list.append(extract_words(text))
    cleaned_list=[]
    for row in range(len(words_list)):
        for item in range(len(words_list[row])):
            if len(words_list[row][item]) > 2:
                cleaned_list.append(words_list[row][item])
    return(cleaned_list)


In [7]:
cleaned_list = clean_list (tweets_data)

In [8]:
cleaned_list[:9]

['teapainusa',
 'the',
 'cheers',
 'when',
 'you',
 'are',
 'indicted',
 'will',
 'drown']

In [33]:
import re
oscar_nom=re.sub(r'\b\w{1,3}\b', '',"Roma Green Book Black Panther BlacKkKlansman Bohemian Rhapsody A Star Is Born Vice")
oscar_nominees = extract_words(oscar_nom)

In [34]:
oscar_nominees

['roma',
 'green',
 'book',
 'black',
 'panther',
 'blackkklansman',
 'bohemian',
 'rhapsody',
 'star',
 'born',
 'vice']

In [35]:
'''
'Roma' 426426
'Green Book' 490132
'The Favourite' 375262
'Bohemian Rhapsody' 424694
'Blackkklansman' 487558
'Black Panther' 284054
'A Star is Born' 332562
'Vice' 429197
'''
nom_mvid= [426426,490132,375262,424694,487558,284054,332562,429197]

In [36]:
mv_name=['Roma','Green Book', 'The Favourite', 'Bohemian Rhapsody', 'Blackkklansman', 'Black Panther', 'A Star is Born', 'Vice'] 

In [37]:
movie_tup=[]
for item in range(len(nom_mvid)):
    temp = (mv_name[item],nom_mvid[item])
    movie_tup.append(temp)
movie_tuple=tuple(movie_tup)

In [38]:
(movie_tup[0
          ][1])

426426

In [41]:
for item in range(len(movie_tuple)):
    nom_table=get_nom_data(movie_tuple[item][1])

In [40]:
def get_nom_data(mv_id):
    nom_par = {"api_key": TMDB_KEY}
    base_uri = "https://api.themoviedb.org/3/"
    resource_uri = "movie/" + str(mv_id)
    nom_uri = "/credits"
    nom_data = requests.get(base_uri + resource_uri +nom_uri, params = nom_par)
    nom_table=nom_data.json()
    nom_castcrew=[]
    for row in range(len(nom_table['cast'])):
        if (nom_table['cast'][row]['order'])<5:
            nom_castcrew.append(nom_table['cast'][row]['name'].lower())
    for row in range(len(nom_table['crew'])):
        if nom_table['crew'][row]['job'] == 'Director':
            nom_castcrew.append(nom_table['crew'][row]['name'].lower())        
    return(nom_castcrew)

In [42]:
nom_dict={}
for each_item in range(len(movie_tup)):
    test=[]
    final_list=[]
    temp_movie_data= get_nom_data(movie_tup[each_item][1])
    for element in range(len(temp_movie_data)):
        test=(extract_words(temp_movie_data[element]))
        for elements in range(len(test)):
            if len(test[elements]) > 2:
                final_list.append(test[elements])
    nom_dict[movie_tup[each_item][0]]=final_list

In [43]:
#nom_dict['Roma']=movie_name_variations[0]+nom_dict['Roma']
nom_dict

{'Roma': ['yalitza',
  'aparicio',
  'marina',
  'tavira',
  'diego',
  'cortina',
  'autrey',
  'carlos',
  'peralta',
  'marco',
  'graf',
  'alfonso',
  'cuarón'],
 'Green Book': ['viggo',
  'mortensen',
  'mahershala',
  'ali',
  'linda',
  'cardellini',
  'dimiter',
  'marinov',
  'mike',
  'hatton',
  'peter',
  'farrelly'],
 'The Favourite': ['olivia',
  'colman',
  'emma',
  'stone',
  'rachel',
  'weisz',
  'nicholas',
  'hoult',
  'joe',
  'alwyn',
  'yorgos',
  'lanthimos'],
 'Bohemian Rhapsody': ['rami',
  'malek',
  'gwilym',
  'lee',
  'ben',
  'hardy',
  'joseph',
  'mazzello',
  'lucy',
  'boynton',
  'bryan',
  'singer'],
 'Blackkklansman': ['john',
  'david',
  'washington',
  'adam',
  'driver',
  'laura',
  'harrier',
  'topher',
  'grace',
  'jasper',
  'pääkkönen',
  'spike',
  'lee'],
 'Black Panther': ['chadwick',
  'boseman',
  'michael',
  'jordan',
  'lupita',
  'nyong',
  'danai',
  'gurira',
  'martin',
  'freeman',
  'ryan',
  'coogler'],
 'A Star is Born'

In [44]:
movie_name_variations=[["Roma", "roma"],
    ["Green Book", "green book", "green", "book", "greenbook"],
    ["The Favourite", "the favorite", "the favourite",  "thefavorite" , "favourite", "favorite"],
    ["Bohemian Rhapsody", "bohemian rhapsody", "bohemian", "rhapsody"],
    ["Blackkklansman","blackkklansman"],
    ["Black Panther", "black", "panther", "black panther"],
    ["A Star is Born", "astarisborn", "star", "born"],
    ["Vice", "vice"]]
    

In [45]:
nom_dict

{'Roma': ['yalitza',
  'aparicio',
  'marina',
  'tavira',
  'diego',
  'cortina',
  'autrey',
  'carlos',
  'peralta',
  'marco',
  'graf',
  'alfonso',
  'cuarón'],
 'Green Book': ['viggo',
  'mortensen',
  'mahershala',
  'ali',
  'linda',
  'cardellini',
  'dimiter',
  'marinov',
  'mike',
  'hatton',
  'peter',
  'farrelly'],
 'The Favourite': ['olivia',
  'colman',
  'emma',
  'stone',
  'rachel',
  'weisz',
  'nicholas',
  'hoult',
  'joe',
  'alwyn',
  'yorgos',
  'lanthimos'],
 'Bohemian Rhapsody': ['rami',
  'malek',
  'gwilym',
  'lee',
  'ben',
  'hardy',
  'joseph',
  'mazzello',
  'lucy',
  'boynton',
  'bryan',
  'singer'],
 'Blackkklansman': ['john',
  'david',
  'washington',
  'adam',
  'driver',
  'laura',
  'harrier',
  'topher',
  'grace',
  'jasper',
  'pääkkönen',
  'spike',
  'lee'],
 'Black Panther': ['chadwick',
  'boseman',
  'michael',
  'jordan',
  'lupita',
  'nyong',
  'danai',
  'gurira',
  'martin',
  'freeman',
  'ryan',
  'coogler'],
 'A Star is Born'

In [46]:
for key,i in zip(nom_dict,range(len(movie_name_variations))):
    nom_dict[key] = movie_name_variations[i]+nom_dict[key]

In [47]:
nom_dict

{'Roma': ['Roma',
  'roma',
  'yalitza',
  'aparicio',
  'marina',
  'tavira',
  'diego',
  'cortina',
  'autrey',
  'carlos',
  'peralta',
  'marco',
  'graf',
  'alfonso',
  'cuarón'],
 'Green Book': ['Green Book',
  'green book',
  'green',
  'book',
  'greenbook',
  'viggo',
  'mortensen',
  'mahershala',
  'ali',
  'linda',
  'cardellini',
  'dimiter',
  'marinov',
  'mike',
  'hatton',
  'peter',
  'farrelly'],
 'The Favourite': ['The Favourite',
  'the favorite',
  'the favourite',
  'thefavorite',
  'favourite',
  'favorite',
  'olivia',
  'colman',
  'emma',
  'stone',
  'rachel',
  'weisz',
  'nicholas',
  'hoult',
  'joe',
  'alwyn',
  'yorgos',
  'lanthimos'],
 'Bohemian Rhapsody': ['Bohemian Rhapsody',
  'bohemian rhapsody',
  'bohemian',
  'rhapsody',
  'rami',
  'malek',
  'gwilym',
  'lee',
  'ben',
  'hardy',
  'joseph',
  'mazzello',
  'lucy',
  'boynton',
  'bryan',
  'singer'],
 'Blackkklansman': ['Blackkklansman',
  'blackkklansman',
  'john',
  'david',
  'washing

In [48]:
len(tweets_info)

44366

In [ ]:
for key in nom_dict:
    mentions=0
    for items in range(len(nom_dict[key])):
        for row in range(len(tweets_info)):
            if nom_dict[key][items] in tweets_info[row]:
                    mentions=mentions+1
    print(key,mentions)

In [ ]:
bar_list=[]
for key in nom_dict:
    mentions=0
    for row in range(len(tweets_info)):
        if any(value in tweets_info[row] for value in nom_dict[key]) :
                mentions=mentions+1
    temp_tuple=(key,mentions)
    bar_list.append(temp_tuple)

In [ ]:
bar_list

In [230]:
def get_common(key):
    mv_common_words={}  
    for items in range(len(nom_dict[key])):
        for row in range(len(tweets_info)):
            if nom_dict[key][items] in tweets_info[row]:
                word_count=mv_common_words.get(nom_dict[key][items],0)
                mv_common_words[nom_dict[key][items]]=word_count+1
    plot_list=[]
    new_temp=()
    for key,value in mv_common_words.items():
        new_temp=(key,value)
        plot_list.append(new_temp)
    return (plot_list)
    


In [231]:
word_123=[]
word_123=(get_common('Green Book'))

In [232]:
word_123
    

[('green book', 1048),
 ('green', 1312),
 ('book', 1353),
 ('greenbook', 261),
 ('viggo', 52),
 ('mortensen', 31),
 ('mahershala', 193),
 ('ali', 1500),
 ('linda', 53),
 ('cardellini', 2),
 ('mike', 29),
 ('peter', 146),
 ('farrelly', 13)]

In [ ]:
SENTIMENTS

In [9]:
def words_emotional(emotion_dict):
    emotional_words={}
    for value in EMOTIONS:
        emotional_words[value]=[]
    for key,value in emotion_dict.items():
        for target_key,target_value in emotional_words.items():
            for line_key,line_value in emotion_dict[key].items():
                if line_key==target_key:
                    if key not in emotional_words[target_key]: # Eliminate duplicates
                        emotional_words[target_key].append(key)
    return (emotional_words)

In [10]:
sentiment_dict=words_emotional(SENTIMENTS)

In [ ]:
nom_dict['Green Book']

In [ ]:
row_list=[]
plot_dict={}
for row in range(len(tweets_info)):
    for element in range(len(nom_dict['Green Book'])):
        print(nom_dict['Green Book'][element], tweets_info[row])
        if nom_dict['Green Book'][element] in tweets_info[row]:
            row_list.append(clean_list (tweets_info[row]))
# for key,value in sentiment_dict.items():
#     for each_item in range(len(value)):
#         for each_element in range(len(row_list)):
#             if value[each_item] == row_list[each_element]:
#                 w_count=plot_dict.get(key,0)
#                 plot_dict[key]=w_count+1


'zest'

In [18]:
plot_dict={}
for key,value in sentiment_dict.items():
    for item in range(len(value)):
        for element in range(len(cleaned_list)):
            if value[item] == cleaned_list[element]:
                w_count=plot_dict.get(key,0)
                plot_dict[key]=w_count+1
        print(key,value[item])

positive abba
positive ability
positive abovementioned
positive absolute
positive absolution
positive absorbed
positive abundance
positive abundant
positive academic
positive academy
positive acceptable
positive acceptance
positive accessible
positive accolade
positive accommodation
positive accompaniment
positive accomplish
positive accomplished
positive accomplishment
positive accord
positive accountability
positive accountable
positive accredited
positive accueil
positive accurate
positive ace
positive achieve
positive achievement
positive acknowledgment
positive acquire
positive acquiring
positive acrobat
positive action
positive actual
positive acuity
positive acumen
positive adapt
positive adaptable
positive addresses
positive adept
positive adequacy
positive adjunct
positive admirable
positive admiral
positive admiration
positive admire
positive admirer
positive admissible
positive adorable
positive adoration
positive adore
positive advance
positive advanced
positive advancement

positive completeness
positive completing
positive completion
positive compliance
positive compliant
positive complicity
positive compliment
positive composed
positive composer
positive composure
positive comprehend
positive comprehensive
positive comrade
positive concentric
positive conciliation
positive concluding
positive concord
positive concordance
positive condolence
positive condone
positive conducive
positive conductivity
positive confederate
positive confess
positive confidence
positive confident
positive confirmed
positive conformance
positive congenial
positive congratulatory
positive congregation
positive congruence
positive connoisseur
positive conscience
positive conscientious
positive consciousness
positive consecration
positive conservation
positive conserve
positive considerable
positive considerate
positive consistency
positive console
positive consonant
positive constancy
positive constant
positive constitutional
positive construct
positive consummate
positive contac

positive friendliness
positive friendly
positive friendship
positive frisky
positive frolic
positive frugal
positive fruitful
positive fulfill
positive fulfillment
positive full
positive fully
positive fun
positive fundamental
positive fuse
positive fusion
positive gain
positive gaining
positive gallant
positive gallantry
positive galore
positive garden
positive garnet
positive garrison
positive gazette
positive gear
positive gem
positive general
positive generosity
positive generous
positive genial
positive genius
positive genteel
positive gentleman
positive gentleness
positive gentry
positive genuine
positive geranium
positive gift
positive gifted
positive gigantic
positive giggle
positive girder
positive giving
positive glad
positive gladness
positive glee
positive glide
positive glimmer
positive glittering
positive glorification
positive glorify
positive glory
positive gloss
positive glow
positive glowing
positive god
positive godly
positive godsend
positive gold
positive good
posi

positive missionary
positive model
positive moderate
positive moderator
positive modest
positive modesty
positive momentum
positive monetary
positive money
positive monk
positive monument
positive moral
positive morality
positive morals
positive mortar
positive mother
positive motherhood
positive motive
positive movable
positive mover
positive mug
positive muscular
positive music
positive musical
positive mutable
positive mutual
positive nap
positive naturalist
positive navigable
positive neatly
positive nectar
positive needle
positive negotiate
positive negotiator
positive neighbor
positive nerve
positive nestle
positive nobility
positive noble
positive nobleman
positive nomination
positive normality
positive notable
positive notables
positive noted
positive notion
positive notoriety
positive nourishment
positive numbers
positive nurse
positive nursery
positive nurture
positive nutritious
positive oak
positive oasis
positive oath
positive obedience
positive objective
positive obliging

positive reunion
positive revel
positive revels
positive revere
positive reverence
positive reverend
positive reverie
positive revise
positive revival
positive revive
positive revolution
positive revolutionary
positive reward
positive rhythm
positive rhythmical
positive ribbon
positive richness
positive rider
positive righteous
positive rightful
positive rightly
positive ripe
positive ripen
positive rising
positive riveting
positive roadster
positive robust
positive rock
positive rod
positive rollicking
positive romance
positive romantic
positive romanticism
positive romp
positive rooted
positive rosy
positive rota
positive routine
positive royalty
positive rubric
positive ruth
positive safe
positive safeguard
positive sage
positive saint
positive saintly
positive salary
positive salient
positive salutary
positive salute
positive salvation
positive salve
positive samurai
positive sanctification
positive sanctify
positive sanctuary
positive sanguine
positive sanitary
positive satin
posi

...

sadness enslaved
sadness entangled
sadness epidemic
sadness epitaph
sadness error
sadness eschew
sadness esteem
sadness euthanasia
sadness evanescence
sadness evasion
sadness evict
sadness eviction
sadness evil
sadness excluded
sadness excluding
sadness exclusion
sadness execution
sadness executioner
sadness exhausted
sadness exhaustion
sadness exile
sadness exorcism
sadness expel
sadness expire
sadness explode
sadness expulsion
sadness exterminate
sadness extinct
sadness failing
sadness failure
sadness fainting
sadness faithless
sadness fall
sadness falling
sadness famine
sadness fasting
sadness fat
sadness fatal
sadness fatality
sadness fatigued
sadness fatty
sadness fault
sadness fearful
sadness fearfully
sadness feeble
sadness feeling
sadness fell
sadness feudalism
sadness flaccid
sadness flaw
sadness fleece
sadness flinch
sadness flog
sadness flop
sadness flounder
sadness forbid
sadness foreclose
sadness forfeit
sadness forfeiture
sadness forgotten
sadness forlorn
sadness forsake


sadness rot
sadness rubble
sadness rue
sadness ruin
sadness ruined
sadness ruinous
sadness rumor
sadness runaway
sadness rupture
sadness sabotage
sadness sacrifices
sadness sadly
sadness sadness
sadness sanctify
sadness sap
sadness sarcasm
sadness sarcoma
sadness savor
sadness scar
sadness scarce
sadness scarcely
sadness scarcity
sadness schizophrenia
sadness scold
sadness scourge
sadness scrapie
sadness secluded
sadness sedition
sadness segregate
sadness senile
sadness senseless
sadness sentence
sadness sepsis
sadness sequestration
sadness seriousness
sadness servile
sadness setback
sadness severance
sadness shack
sadness shackle
sadness shame
sadness shameful
sadness shatter
sadness shattered
sadness shell
sadness shipwreck
sadness shiver
sadness shortage
sadness shot
sadness shriek
sadness shrink
sadness shroud
sadness shun
sadness sick
sadness sickening
sadness sickly
sadness sickness
sadness sin
sadness sinful
sadness sing
sadness sinner
sadness sisterhood
sadness skid
sadness sla

surprise grin
surprise guess
surprise gulp
surprise hap
surprise hermaphrodite
surprise hero
surprise heroic
surprise heroism
surprise highest
surprise hilarious
surprise hoax
surprise holiness
surprise honeymoon
surprise hope
surprise hopeful
surprise horde
surprise horror
surprise howl
surprise humanitarian
surprise hypertrophy
surprise hypothesis
surprise illegitimate
surprise illuminate
surprise illumination
surprise illusion
surprise immediacy
surprise immerse
surprise improvisation
surprise improvise
surprise incendiary
surprise incident
surprise incontinence
surprise independence
surprise inexplicable
surprise infant
surprise infarct
surprise infrequent
surprise inheritance
surprise insolvency
surprise inspired
surprise insult
surprise intense
surprise interrupt
surprise intrigue
surprise intruder
surprise intrusive
surprise invade
surprise invite
surprise inviting
surprise jackpot
surprise jerk
surprise jest
surprise joker
surprise jolt
surprise jubilant
surprise jubilee
surpri

trust bride
trust bridegroom
trust bridesmaid
trust brighten
trust brilliant
trust brother
trust brotherhood
trust brotherly
trust buddy
trust budget
trust bureaucracy
trust bursary
trust butler
trust bylaw
trust cabinet
trust calculator
trust calf
trust calls
trust candid
trust canons
trust cap
trust captivate
trust caretaker
trust carol
trust cash
trust cashier
trust cathedral
trust cautious
trust celebration
trust celebrity
trust cement
trust censor
trust center
trust certify
trust chairman
trust chairwoman
trust champion
trust chancellor
trust chaplain
trust charitable
trust chart
trust chastity
trust checklist
trust cheer
trust cheerfulness
trust chemist
trust cherish
trust chicane
trust chocolate
trust choir
trust chronicle
trust chuckle
trust church
trust civilization
trust civilized
trust clan
trust clap
trust clean
trust clearance
trust clerical
trust climax
trust closeness
trust coach
trust coalesce
trust coax
trust coexist
trust coexisting
trust cogent
trust cohesion
trust c

trust legalized
trust legislator
trust legislature
trust legitimacy
trust leisure
trust lender
trust lesson
trust lettered
trust levee
trust level
trust libel
trust liberate
trust liberty
trust lieutenant
trust liking
trust linguist
trust lodging
trust lord
trust lovable
trust lovely
trust lovemaking
trust lover
trust loving
trust loyal
trust loyalty
trust machine
trust magnet
trust magnificence
trust magnificent
trust mainstay
trust maintenance
trust majestic
trust majesty
trust majority
trust mamma
trust manage
trust management
trust mandarin
trust manual
trust marine
trust marriage
trust marrow
trust marry
trust marshal
trust mastery
trust mate
trust mathematical
trust matrimony
trust matron
trust maxim
trust measure
trust measured
trust medal
trust mediate
trust mediator
trust medical
trust meditate
trust memorable
trust mentor
trust merchant
trust merit
trust meritorious
trust messenger
trust microscope
trust midwife
trust mighty
trust ministry
trust miracle
trust mislead
trust mo

In [19]:
plot_dict

{'positive': 25432,
 'negative': 9699,
 'anger': 4736,
 'anticipation': 11130,
 'disgust': 3551,
 'fear': 5379,
 'joy': 13626,
 'sadness': 5335,
 'surprise': 8064,
 'trust': 13279}

In [20]:
len(cleaned_list)

518940

In [29]:
frame=[]
for key in plot_dict:
    pcent=round((plot_dict[key]/len(cleaned_list))*100,2)
    percent=str(pcent)+'%'
    tup_temp=(key,percent)
    frame.append(tup_temp)
sorted_frame= sorted(frame, key=operator.itemgetter(1), reverse=True)

In [85]:
print("{0:<16} {1:<12}".format('EMOTION','% WORDS'))
for row in range(len(sorted_frame)):
        print("{0:<16} {1:<12}".format(sorted_frame[row][0],sorted_frame[row][1]))

EMOTION          % WORDS     
positive         4.9%        
joy              2.63%       
trust            2.56%       
anticipation     2.14%       
negative         1.87%       
surprise         1.55%       
fear             1.04%       
sadness          1.03%       
anger            0.91%       
disgust          0.68%       


In [58]:
def movie_senti(key,tweets_info,nom_dict):
    movie_mentions=[]
    for row in range(len(tweets_info)):
        if any(value in tweets_info[row] for value in nom_dict[key]) :
                movie_mentions.append(tweets_info[row])
    return movie_mentions


In [59]:
movie_mentions=[]

In [60]:
movie_mentions=[]
movie_mentions=movie_senti('Green Book',tweets_info,nom_dict)
movie_senti_list = clean_list (movie_mentions)

In [233]:
movie_mentions

['rt @mefeater: congrats to mahershala ali on winning best actor in a supporting role for his role in ‘green book’ #oscars 🖤 https://t.co/sn0…',
 "rt @seriestwbz: green book: o guia venceu na categoria 'melhor filme' no #oscars https://t.co/yuwdntvojk",
 "rt @espn: before becoming a two-time #oscars winner, mahershala ali (then gilmore) played d-i basketball at st. mary's from 1992-96. (via @…",
 'rt @realcandaceo: just turned on the #oscars for exactly one minute. caught the tail-end of a speech about “menstruation equality” and femi…',
 'rt @sadolphy: chadwick boseman when green book won lmao #oscars https://t.co/b5oprdkk4z',
 'rt @larryelder: hollywood soldiers arrive to battle "inequality."\n\n#oscars \n\n(photo from @thebabylonbee) https://t.co/qn175avwjt',
 'rt @sadolphy: chadwick boseman when green book won lmao #oscars https://t.co/b5oprdkk4z',
 'rt @proudresister: black panther won the popular vote and green book won the electoral college. #oscars',
 'rt @realcandaceo: just tu

In [62]:
movie_senti_list = clean_list (movie_mentions)

In [73]:
len(movie_senti_list)

43753

In [67]:
plot_moviedict={}
for key,value in sentiment_dict.items():
    for item in range(len(value)):
        for element in range(len(movie_senti_list)):
            if value[item] == movie_senti_list[element]:
                w_count=plot_moviedict.get(key,0)
                plot_moviedict[key]=w_count+1
        print(key,value[item])

positive abba
positive ability
positive abovementioned
positive absolute
positive absolution
positive absorbed
positive abundance
positive abundant
positive academic
positive academy
positive acceptable
positive acceptance
positive accessible
positive accolade
positive accommodation
positive accompaniment
positive accomplish
positive accomplished
positive accomplishment
positive accord
positive accountability
positive accountable
positive accredited
positive accueil
positive accurate
positive ace
positive achieve
positive achievement
positive acknowledgment
positive acquire
positive acquiring
positive acrobat
positive action
positive actual
positive acuity
positive acumen
positive adapt
positive adaptable
positive addresses
positive adept
positive adequacy
positive adjunct
positive admirable
positive admiral
positive admiration
positive admire
positive admirer
positive admissible
positive adorable
positive adoration
positive adore
positive advance
positive advanced
positive advancement

positive compliment
positive composed
positive composer
positive composure
positive comprehend
positive comprehensive
positive comrade
positive concentric
positive conciliation
positive concluding
positive concord
positive concordance
positive condolence
positive condone
positive conducive
positive conductivity
positive confederate
positive confess
positive confidence
positive confident
positive confirmed
positive conformance
positive congenial
positive congratulatory
positive congregation
positive congruence
positive connoisseur
positive conscience
positive conscientious
positive consciousness
positive consecration
positive conservation
positive conserve
positive considerable
positive considerate
positive consistency
positive console
positive consonant
positive constancy
positive constant
positive constitutional
positive construct
positive consummate
positive contact
positive contemplation
positive content
positive continue
positive contour
positive contribute
positive contributor
pos

positive gain
positive gaining
positive gallant
positive gallantry
positive galore
positive garden
positive garnet
positive garrison
positive gazette
positive gear
positive gem
positive general
positive generosity
positive generous
positive genial
positive genius
positive genteel
positive gentleman
positive gentleness
positive gentry
positive genuine
positive geranium
positive gift
positive gifted
positive gigantic
positive giggle
positive girder
positive giving
positive glad
positive gladness
positive glee
positive glide
positive glimmer
positive glittering
positive glorification
positive glorify
positive glory
positive gloss
positive glow
positive glowing
positive god
positive godly
positive godsend
positive gold
positive good
positive goodly
positive goodness
positive goods
positive goodwill
positive gorgeous
positive gospel
positive govern
positive grace
positive graceful
positive gracious
positive graciously
positive graduation
positive grandchildren
positive grandeur
positive gra

positive mutable
positive mutual
positive nap
positive naturalist
positive navigable
positive neatly
positive nectar
positive needle
positive negotiate
positive negotiator
positive neighbor
positive nerve
positive nestle
positive nobility
positive noble
positive nobleman
positive nomination
positive normality
positive notable
positive notables
positive noted
positive notion
positive notoriety
positive nourishment
positive numbers
positive nurse
positive nursery
positive nurture
positive nutritious
positive oak
positive oasis
positive oath
positive obedience
positive objective
positive obliging
positive observant
positive obtainable
positive obvious
positive occupant
positive occupation
positive occupy
positive offer
positive officer
positive offset
positive offshoot
positive omnipotence
positive omniscient
positive openness
positive opera
positive opportune
positive opportunity
positive optimism
positive optimist
positive option
positive optional
positive oracle
positive oration
positi

positive rota
positive routine
positive royalty
positive rubric
positive ruth
positive safe
positive safeguard
positive sage
positive saint
positive saintly
positive salary
positive salient
positive salutary
positive salute
positive salvation
positive salve
positive samurai
positive sanctification
positive sanctify
positive sanctuary
positive sanguine
positive sanitary
positive satin
positive satisfactorily
positive satisfied
positive save
positive savings
positive savor
positive savory
positive savvy
positive scarecrow
positive scholar
positive scholarship
positive scientific
positive scientist
positive scintilla
positive score
positive scribe
positive script
positive scrumptious
positive sculpture
positive sea
positive seal
positive seasoned
positive seclusion
positive secretariat
positive seniority
positive sensational
positive sense
positive sensibility
positive sensibly
positive sensual
positive sensuality
positive sensuous
positive sentimental
positive sentimentality
positive sen

...

sadness lonely
sadness lonesome
sadness longing
sadness lose
sadness losing
sadness loss
sadness lost
sadness lovely
sadness lower
sadness lowest
sadness lowly
sadness lunacy
sadness lush
sadness lynch
sadness mad
sadness malaise
sadness malaria
sadness malevolent
sadness malicious
sadness malignancy
sadness mangle
sadness manslaughter
sadness margin
sadness martyr
sadness martyrdom
sadness massacre
sadness mausoleum
sadness meaningless
sadness measles
sadness meek
sadness melancholic
sadness melancholy
sadness melodrama
sadness meltdown
sadness memorials
sadness militia
sadness miscarriage
sadness miserable
sadness miserably
sadness misery
sadness misfortune
sadness mishap
sadness misrepresentation
sadness missing
sadness mistake
sadness misunderstanding
sadness moan
sadness mocking
sadness molestation
sadness monsoon
sadness moody
sadness morbid
sadness morbidity
sadness morgue
sadness moribund
sadness mortality
sadness mortification
sadness mortuary
sadness mother
sadness mourn
sadn

sadness worthless
sadness wound
sadness wrangling
sadness wreck
sadness wrecked
sadness wretch
sadness wretched
sadness wrinkled
sadness wrongdoing
sadness wrongful
sadness wrongly
surprise abandonment
surprise abduction
surprise abrupt
surprise accident
surprise accidental
surprise accidentally
surprise accolade
surprise advance
surprise affront
surprise aghast
surprise alarm
surprise alarming
surprise alertness
surprise alerts
surprise allure
surprise amaze
surprise amazingly
surprise ambush
surprise angel
surprise anomaly
surprise apparition
surprise applause
surprise art
surprise aspiration
surprise assail
surprise assessment
surprise astonishingly
surprise astonishment
surprise attacking
surprise avalanche
surprise award
surprise bang
surprise banger
surprise betray
surprise bewildered
surprise bewilderment
surprise birthday
surprise bizarre
surprise blast
surprise blessings
surprise blindfold
surprise blitz
surprise bloodshed
surprise bomb
surprise bonus
surprise break
surprise b

surprise trick
surprise trickery
surprise trip
surprise trophy
surprise trump
surprise tumult
surprise unanticipated
surprise unbeaten
surprise unbridled
surprise uncanny
surprise uncertain
surprise uncontrollable
surprise uncover
surprise underestimate
surprise undiscovered
surprise unexpected
surprise unexpectedly
surprise unforeseen
surprise unfulfilled
surprise unguarded
surprise unimaginable
surprise unintended
surprise unintentional
surprise unintentionally
surprise unique
surprise unprecedented
surprise unpredictable
surprise unstable
surprise unsuspecting
surprise urgency
surprise urgent
surprise vanish
surprise vanished
surprise variable
surprise veer
surprise veracity
surprise victimized
surprise violation
surprise violent
surprise visor
surprise volatility
surprise volcano
surprise vote
surprise warn
surprise warned
surprise weight
surprise whim
surprise wild
surprise wildfire
surprise winner
surprise winning
surprise wireless
surprise wizard
surprise wonderful
surprise wond

trust fidelity
trust fiesta
trust fill
trust finally
trust fireman
trust firmness
trust firstborn
trust fitting
trust fixed
trust flagship
trust flange
trust flirt
trust follower
trust food
trust footing
trust forecast
trust forefathers
trust foresee
trust foresight
trust forgiving
trust formality
trust formative
trust formula
trust fort
trust fortitude
trust fortress
trust fortune
trust found
trust framework
trust frank
trust frankness
trust fraternal
trust freedom
trust freely
trust friend
trust friendliness
trust friendly
trust friendship
trust fugitive
trust fulfillment
trust fully
trust fundamental
trust fuse
trust gage
trust garrison
trust gate
trust gateway
trust gauging
trust gazette
trust general
trust generosity
trust generous
trust gentleman
trust gentry
trust genuine
trust girder
trust glorify
trust glory
trust glow
trust god
trust godly
trust good
trust goodness
trust gospel
trust govern
trust governess
trust governor
trust graduation
trust grammar
trust grandchildren
trus

trust spaniel
trust specialist
trust specialize
trust spokesman
trust sponsor
trust spotless
trust spouse
trust stable
trust stamina
trust star
trust stark
trust statement
trust statistical
trust steadfast
trust steady
trust sterling
trust steward
trust straightforward
trust strategist
trust strength
trust strengthening
trust structural
trust structure
trust substantiate
trust succeed
trust succeeding
trust successful
trust suggest
trust sun
trust sundial
trust superman
trust superstar
trust supplication
trust supporter
trust supporting
trust supremacy
trust surety
trust surrogate
trust swear
trust sweet
trust sweetheart
trust symmetry
trust sympathetic
trust synchronize
trust synergistic
trust synod
trust synonymous
trust system
trust tactics
trust tandem
trust tantamount
trust taught
trust teach
trust teacher
trust team
trust temperate
trust tender
trust testament
trust testimony
trust theocratic
trust theological
trust theorem
trust theory
trust therapeutic
trust thermometer
trust t

In [68]:
plot_moviedict

{'positive': 3503,
 'negative': 1153,
 'anger': 478,
 'anticipation': 706,
 'disgust': 396,
 'fear': 428,
 'joy': 1993,
 'sadness': 939,
 'surprise': 426,
 'trust': 1987}

In [71]:
moviedict = sorted(plot_moviedict.items(), key=operator.itemgetter(1), reverse=True)

In [81]:
len(moviedict)

10

In [89]:
dframe=[]
for rows in range(len(moviedict)):
    prcent=round((moviedict[rows][1]/len(movie_senti_list))*100,2)
    percentage=str(prcent)+'%'
    tuple_temp=(moviedict[rows][0],percentage)
    dframe.append(tuple_temp)
sorted_mv_senti= sorted(dframe, key=operator.itemgetter(1), reverse=True)

print("{0:<16} {1:<12}".format('EMOTION','% WORDS'))
for row in range(len(sorted_mv_senti)):
    print("{0:<16} {1:<12}".format(sorted_mv_senti[row][0],sorted_mv_senti[row][1]))

EMOTION          % WORDS     
positive         8.01%       
joy              4.56%       
trust            4.54%       
negative         2.64%       
sadness          2.15%       
anticipation     1.61%       
anger            1.09%       
fear             0.98%       
surprise         0.97%       
disgust          0.91%       


In [97]:
time_data=[]
for row in range(len(csv_data)):
    temp_time=(csv_data[row][0],csv_data[row][3])
    time_data.append(temp_time)

In [103]:
len(time_data[0][0])

30

In [104]:
time_data[0][0]

'Mon Feb 25 13:15:07 +0000 2019'

In [141]:
daytime=time_data[0][0][11:16]

In [142]:
daytime

'13:15'

In [121]:
date

'25'

In [143]:
def tweet_trends(key,time_data,nom_dict):
    tweet_mentions=[]
    for row in range(len(time_data)):
        if any(nvalue in time_data[row][1] for nvalue in nom_dict[key]) :
            daytime=time_data[row][0][11:16]
            trends_temp=(daytime,key)
            tweet_mentions.append(trends_temp)
    return tweet_mentions

In [144]:
tweet_mentions2=tweet_trends('Vice',time_data,nom_dict)

In [234]:
(tweet_mentions2)

[('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),


In [146]:
tweet_mentions2

[('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:15', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),
 ('13:16', 'Vice'),


In [150]:
def get_count(tweet_mentions2):
    print_trend={}
    current=tweet_mentions2[0][0]
    for each_row in range(len(tweet_mentions2)):
        if tweet_mentions2[each_row][0] == current:
            count=print_trend.get(tweet_mentions2[each_row][0],0)
            print_trend[tweet_mentions2[each_row][0]]=count+1
        else:
            current=tweet_mentions2[each_row][0]
    return(print_trend)
            
            

In [151]:
print_trend=get_count(tweet_mentions2)

In [153]:
def dict2list(sample_dict):
    sample_list=[]
    for key,value in sample_dict.items():
        temp=(key,value)
        sample_list.append(temp)
    return (sample_list)

In [155]:
plot_trend=dict2list(print_trend)

In [156]:
plot_trend

[('13:15', 32),
 ('13:16', 38),
 ('13:17', 27),
 ('13:18', 29),
 ('13:19', 34),
 ('13:20', 27),
 ('13:21', 27),
 ('13:22', 30),
 ('13:23', 21),
 ('13:24', 28),
 ('13:25', 24),
 ('13:26', 27),
 ('13:27', 35),
 ('13:28', 25),
 ('13:29', 29),
 ('13:30', 26),
 ('13:31', 8)]

In [158]:
def sentiment_trends(key,time_data,nom_dict):
    sentiment_trend=[]
    for row in range(len(time_data)):
        if any(nvalue in time_data[row][1] for nvalue in nom_dict[key]) :
            daytime=time_data[row][0][11:16]
            trends_temp=(daytime,time_data[row][1])
            sentiment_trend.append(trends_temp)
    return sentiment_trend

In [159]:
sentiment_trend =sentiment_trends('Green Book',time_data,nom_dict)

In [235]:
sentiment_trend[:3]

[('13:15',
  'RT @mefeater: Congrats to Mahershala Ali on winning Best Actor in a Supporting Role for his role in ‘Green Book’ #Oscars 🖤 https://t.co/sN0…'),
 ('13:15',
  "RT @SeriesTWBZ: Green Book: O Guia venceu na categoria 'Melhor Filme' no #Oscars https://t.co/yUwDnTVoJK"),
 ('13:15',
  'RT @RealCandaceO: Just turned on the #Oscars for exactly one minute. Caught the tail-end of a speech about “menstruation equality” and femi…')]

In [224]:
def each_row_analysis(sample_string):
    current_time=sample_string[0][0]
    emotional_words={}
    trend_clean=[]
    final_trend=[]
    for row in range(len(sample_string)):
        if sample_string[row][0] ==current_time:
            trend_clean.append(clean_list2(sentiment_trend[row][1]))
            for words in trend_clean:
                for key,value in sentiment_dict.items():
                    for each_val in value:
                        #print(each_val,words)
                        if each_val in words:
                            count=emotional_words.get(key,0)
                            emotional_words[key]=count+1
        else:
            current_time= sample_string[row][0]
        temp_line=(sample_string[row][0],emotional_words)
        final_trend.append(temp_line)
    return(final_trend)

In [223]:
sentiment_trend[0]

('13:15',
 'RT @mefeater: Congrats to Mahershala Ali on winning Best Actor in a Supporting Role for his role in ‘Green Book’ #Oscars 🖤 https://t.co/sN0…')

In [228]:
#abcd=each_row_analysis(sentiment_trend)
abcd

NameError: name 'abcd' is not defined

In [226]:
abcd

NameError: name 'abcd' is not defined

In [217]:

for row in range(len(sentiment_trend)):
    trend_clean.append(clean_list2(sentiment_trend[row][1]))
for words in trend_clean:
    for key,value in sentiment_dict.items():
        for each_val in value:
            print(each_val,words)
            if each_val in words:
                count=emotional_words.get(key,0)
                emotional_words[key]=count+1

abba ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
ability ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
abovementioned ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
absolute ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
absolution ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
absorbed ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
abundance ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best'

grin ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
grist ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
grit ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
groundwork ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
grow ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
growth ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
guarantee ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'suppor

recorder ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
recoup ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
recovery ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
recreation ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
recreational ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
rectify ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
redemption ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best

butt ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
buzzed ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
cabal ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
cacophony ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
cad ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
cadaver ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
cage ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting

flabby ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flaccid ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flagging ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flagrant ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flake ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flap ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', 'supporting', 'role', 'for', 'his', 'role', 'green', 'book', 'oscars']
flatulence ['mefeater', 'congrats', 'mahershala', 'ali', 'winning', 'best', 'actor', '

...

coercion ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
coffin ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
cold ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
coldly ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
coldness ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
colic ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
collapse ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
collision ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
collusion ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
coma ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
comatose ['sadolphy', 'chadwick', 'boseman', 'when', 'green', '

hostage ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
hostile ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
hostilities ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
hostility ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
howl ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
huff ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
humble ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
humbug ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
humiliate ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
humiliating ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
humiliation ['sadolphy', 'chadwick', 'boseman', 'when', 

resisting ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
restrain ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
restrict ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
restriction ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
restrictive ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
retaliate ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
retaliation ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
retaliatory ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
retard ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
retardation ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
reticent ['sadolphy', 'chadwick', '

bombard ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
bombardment ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
bothering ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
bout ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
boxing ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
brawl ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
brazen ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
brimstone ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
broil ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
broken ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'book', 'won', 'lmao', 'oscars']
brunt ['sadolphy', 'chadwick', 'boseman', 'when', 'green', 'bo

KeyboardInterrupt: 

In [218]:
emotional_words

{'positive': 7,
 'anticipation': 1,
 'disgust': 1,
 'joy': 4,
 'sadness': 1,
 'surprise': 1,
 'trust': 5}

In [200]:
def clean_list2 (tweets_data):
    words_list=[]
    #for text in tweets_data:
    words_list.append(extract_words2(tweets_data))
    cleaned_list=[]
    for row in range(len(words_list)):
        for item in range(len(words_list[row])):
            if len(words_list[row][item]) > 2:
                if not words_list[row][item] == 'https':
                    cleaned_list.append(words_list[row][item])
    return(cleaned_list)

In [201]:
def extract_words2(text):
    raw_words = word_tokenize(text)
    words = []
    for word in raw_words:
        if(word[0].isalpha()):
            words.append(word.lower())
    return words